In [ ]:
import os
import sys
import yaml
import types
import pprint
from autogen_agentchat.teams import SelectorGroupChat
from autogen_agentchat.conditions import MaxMessageTermination, TextMentionTermination
from autogen_agentchat.ui import Console
from autogen_ext.memory.canvas import TextCanvasMemory


# Project import paths
# Get the current directory (which is project/test)
notebook_dir = os.getcwd()

# Compute absolute paths for lib and src (one level up from test/)
lib_path = os.path.abspath(os.path.join(notebook_dir, '..', 'lib'))
src_path = os.path.abspath(os.path.join(notebook_dir, '..', 'src'))

sys.path.append(lib_path)
sys.path.append(src_path)

from agents_creator import create_agents_from_config
from rag_helpers import rag_indexer_runner
from model_loader import load_model_client

2025-07-10 16:40:28 - USER_AGENT environment variable not set, consider setting it to identify your requests.


In [2]:
rag_vector_memory = await rag_indexer_runner('/run/media/jun/Jun 6T/Code/TFM_BA_GPT/lib/rag_config.yaml')

/run/media/jun/Jun 6T/Code/TFM_BA_GPT/venv/lib/python3.13/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


2025-07-10 16:40:37 - Load pretrained SentenceTransformer: paraphrase-multilingual-mpnet-base-v2
✅ All documents and URLs are already indexed.


2025-07-10 16:40:42 - Exception while exporting Span.
Traceback (most recent call last):
  File "/run/media/jun/Jun 6T/Code/TFM_BA_GPT/venv/lib/python3.13/site-packages/urllib3/connection.py", line 198, in _new_conn
    sock = connection.create_connection(
        (self._dns_host, self.port),
    ...<2 lines>...
        socket_options=self.socket_options,
    )
  File "/run/media/jun/Jun 6T/Code/TFM_BA_GPT/venv/lib/python3.13/site-packages/urllib3/util/connection.py", line 85, in create_connection
    raise err
  File "/run/media/jun/Jun 6T/Code/TFM_BA_GPT/venv/lib/python3.13/site-packages/urllib3/util/connection.py", line 73, in create_connection
    sock.connect(sa)
    ~~~~~~~~~~~~^^^^
ConnectionRefusedError: [Errno 111] Connection refused

The above exception was the direct cause of the following exception:

Traceback (most recent call last):
  File "/run/media/jun/Jun 6T/Code/TFM_BA_GPT/venv/lib/python3.13/site-packages/urllib3/connectionpool.py", line 787, in urlopen
    response

In [3]:
# 1. Create the canvas memory and tool:
text_canvas_memory = TextCanvasMemory()
update_file_tool = text_canvas_memory.get_update_file_tool()

# 2. Register the tool as 'canvas.update_file_tool' for YAML import:
canvas = types.SimpleNamespace()
canvas.update_file_tool = update_file_tool
sys.modules['canvas'] = canvas  # This enables the tool import by your agent factory!

In [4]:
model_client = load_model_client("azure")

In [5]:
# Construct the absolute path to project/lib/agents_config.yaml
AGENTS_CONFIG = os.path.abspath(os.path.join(notebook_dir, '..', 'lib', 'agents_config.yaml'))
with open(AGENTS_CONFIG, "r") as f:
        config_yaml = yaml.safe_load(f)
agent_names = list(config_yaml.keys())

user_proxy, agents = await create_agents_from_config(
    AGENTS_CONFIG,
    agent_names=agent_names,
    model_client=model_client,
    vector_memory=rag_vector_memory,
    canvas_memory=text_canvas_memory,
    input_func=input
)

In [6]:
for name, agent in agents.items():
    print(f"\n--- Agent: {name} ---")
    pprint.pprint(vars(agent))




--- Agent: planning_agent ---
{'_description': 'An agent for planning tasks, this agent should be the first '
                 'to engage when given a new task.',
 '_handoff_tools': [],
 '_handoffs': {},
 '_is_running': False,
 '_max_tool_iterations': 1,
 '_memory': None,
 '_metadata': {},
 '_model_client': <autogen_ext.models.openai._openai_client.AzureOpenAIChatCompletionClient object at 0x7f0d5ad04c20>,
 '_model_client_stream': False,
 '_model_context': <autogen_core.model_context._unbounded_chat_completion_context.UnboundedChatCompletionContext object at 0x7f0d5aba9940>,
 '_name': 'planning_agent',
 '_output_content_type': None,
 '_output_content_type_format': None,
 '_reflect_on_tool_use': False,
 '_structured_message_factory': None,
 '_system_messages': [SystemMessage(content='You are a planning agent.\nYour job is to break down complex tasks into smaller, manageable subtasks.\nYour team members are:\n  - interviewer_agent\n  - summarizer_agent\n  - funct_spec_checker_agent\n  -

In [7]:
selector_prompt = """Select an agent to perform task.

{roles}

Current conversation context:
{history}

Read the above conversation, then select an agent from {participants} to perform the next task.
Make sure the planner agent has assigned tasks before other agents start working.
Only select one agent.
"""

In [8]:
# Order agents (workflow order), user_proxy last
agent_order = [
    "planning_agent",
    "interviewer_agent",
    "summarizer_agent",
    "doc_writter_agent",
    "funct_spec_checker_agent",
    "diagram_creator_agent",
    "mermaid_code_reviewer_agent"
]
member_agents = [agents[name] for name in agent_order if name in agents] + [user_proxy]

In [9]:
termination = MaxMessageTermination(100000000) | TextMentionTermination("TERMINATE")

# --- Use SelectorGroupChat ---
team = SelectorGroupChat(
    member_agents,
    model_client=model_client,
    termination_condition=termination,
    selector_prompt=selector_prompt,
    allow_repeated_speaker=True
)

In [10]:
task = "Write the functional specifications for a new product"

In [11]:
await Console(team.run_stream(task=task))

2025-07-10 16:40:41 - {"payload": "{\"messages\":[{\"id\":\"3c6a8bf3-c44a-4909-8364-1464d509ccf6\",\"source\":\"user\",\"models_usage\":null,\"metadata\":{},\"created_at\":\"2025-07-10T14:40:41.210209Z\"}],\"output_task_messages\":true}", "sender": null, "receiver": "SelectorGroupChatManager_e5b1cbb9-01b7-44bb-a4af-7d2d97548f28/e5b1cbb9-01b7-44bb-a4af-7d2d97548f28", "kind": "MessageKind.DIRECT", "delivery_stage": "DeliveryStage.SEND", "type": "Message"}
2025-07-10 16:40:41 - Sending message of type GroupChatStart to SelectorGroupChatManager_e5b1cbb9-01b7-44bb-a4af-7d2d97548f28: {'messages': [TextMessage(id='3c6a8bf3-c44a-4909-8364-1464d509ccf6', source='user', models_usage=None, metadata={}, created_at=datetime.datetime(2025, 7, 10, 14, 40, 41, 210209, tzinfo=datetime.timezone.utc), content='Write the functional specifications for a new product', type='TextMessage')], 'output_task_messages': True}
2025-07-10 16:40:41 - Calling message handler for SelectorGroupChatManager_e5b1cbb9-01b7-

/run/media/jun/Jun 6T/Code/TFM_BA_GPT/venv/lib/python3.13/site-packages/autogen_agentchat/teams/_group_chat/_selector_group_chat.py:270: UserWarning: Resolved model mismatch: gpt-4o-2024-08-06 != gpt-4o-2024-11-20. Model mapping in autogen_ext.models.openai may be incorrect. Set the model to gpt-4o-2024-11-20 to enhance token/cost estimation and suppress this warning.
  response = await self._model_client.create(messages=select_speaker_messages)


2025-07-10 16:40:45 - HTTP Request: POST https://224d2-m9kjdmy0-eastus2.openai.azure.com/openai/deployments/gpt-4o/chat/completions?api-version=2024-12-01-preview "HTTP/1.1 200 OK"
2025-07-10 16:40:45 - {"tools": [], "type": "LLMCall", "messages": [{"content": "You are a planning agent.\nYour job is to break down complex tasks into smaller, manageable subtasks.\nYour team members are:\n  - interviewer_agent\n  - summarizer_agent\n  - funct_spec_checker_agent\n  - diagram_creator_agent\n  - mermaid_code_reviewer_agent\nYou only plan and delegate tasks - you do not execute them yourself.\nWhen assigning tasks, use this format:\n1. <agent> : <task>\nAfter assigning tasks, wait for all agents to finish their tasks.\nWhen an Agent finish their task, they will send a message to you with the result and the word \"READY\"\nYou will then summarize the results and hand off to the next agent in the workflow.\nAfter all tasks are complete, summarize the findings and end with \"TERMINATE\".\n", "ro

/run/media/jun/Jun 6T/Code/TFM_BA_GPT/venv/lib/python3.13/site-packages/autogen_agentchat/agents/_assistant_agent.py:1118: UserWarning: Resolved model mismatch: gpt-4o-2024-08-06 != gpt-4o-2024-11-20. Model mapping in autogen_ext.models.openai may be incorrect. Set the model to gpt-4o-2024-11-20 to enhance token/cost estimation and suppress this warning.
  model_result = await model_client.create(


2025-07-10 16:40:45 - HTTP Request: POST https://224d2-m9kjdmy0-eastus2.openai.azure.com/openai/deployments/gpt-4o/chat/completions?api-version=2024-12-01-preview "HTTP/1.1 200 OK"
2025-07-10 16:40:45 - {"tools": [], "type": "LLMCall", "messages": [{"content": "Select an agent to perform task.\n\nplanning_agent: An agent for planning tasks, this agent should be the first to engage when given a new task.\ninterviewer_agent: An agent to ask questions to a human.\nsummarizer_agent: An agent that summarizes information from chats.\nfunct_spec_checker_agent: An agent that checks if the functional specification document is complete.\ndiagram_creator_agent: An agent that creates diagrams as code.\nmermaid_code_reviewer_agent: An agent that reviews Mermaid code.\nuser_proxy: A human user\n\nCurrent conversation context:\nuser: Write the functional specifications for a new product\n\n\nplanning_agent: To write functional specifications for a new product, we need to approach the task in the foll

...

2025-07-10 16:45:22 - HTTP Request: POST https://224d2-m9kjdmy0-eastus2.openai.azure.com/openai/deployments/gpt-4o/chat/completions?api-version=2024-12-01-preview "HTTP/1.1 200 OK"
2025-07-10 16:45:22 - {"type": "LLMStreamStart", "messages": [{"content": "You are an expert on the Mermaid languagge.\n        Review the Diagram Mermaid code stored in \"canvas_diagram.md\" on the canvas.\n        If there is feedback, respond with the feedback.\n        if there is no feedback, writte the code with write_mermaid_to_file to 'disk_diagram.mmd'\n        and respond with 'Diagram code complete' and \"READY\".\n", "role": "system"}, {"role": "user", "name": "user", "content": "Write the functional specifications for a new product"}, {"role": "user", "name": "planning_agent", "content": "To write functional specifications for a new product, we need to approach the task in the following steps:\n\n### Steps to Complete the Task:\n1. Understand the product requirements and objectives, as well as t

/run/media/jun/Jun 6T/Code/TFM_BA_GPT/venv/lib/python3.13/site-packages/autogen_agentchat/teams/_group_chat/_selector_group_chat.py:270: UserWarning: Resolved model mismatch: gpt-4o-2024-08-06 != gpt-4o-2024-11-20. Model mapping in autogen_ext.models.openai may be incorrect. Set the model to gpt-4o-2024-11-20 to enhance token/cost estimation and suppress this warning.
  response = await self._model_client.create(messages=select_speaker_messages)


2025-07-10 16:45:48 - HTTP Request: POST https://224d2-m9kjdmy0-eastus2.openai.azure.com/openai/deployments/gpt-4o/chat/completions?api-version=2024-12-01-preview "HTTP/1.1 200 OK"
2025-07-10 16:45:48 - {"tools": [], "type": "LLMCall", "messages": [{"content": "You are a planning agent.\nYour job is to break down complex tasks into smaller, manageable subtasks.\nYour team members are:\n  - interviewer_agent\n  - summarizer_agent\n  - funct_spec_checker_agent\n  - diagram_creator_agent\n  - mermaid_code_reviewer_agent\nYou only plan and delegate tasks - you do not execute them yourself.\nWhen assigning tasks, use this format:\n1. <agent> : <task>\nAfter assigning tasks, wait for all agents to finish their tasks.\nWhen an Agent finish their task, they will send a message to you with the result and the word \"READY\"\nYou will then summarize the results and hand off to the next agent in the workflow.\nAfter all tasks are complete, summarize the findings and end with \"TERMINATE\".\n", "ro

/run/media/jun/Jun 6T/Code/TFM_BA_GPT/venv/lib/python3.13/site-packages/autogen_agentchat/agents/_assistant_agent.py:1118: UserWarning: Resolved model mismatch: gpt-4o-2024-08-06 != gpt-4o-2024-11-20. Model mapping in autogen_ext.models.openai may be incorrect. Set the model to gpt-4o-2024-11-20 to enhance token/cost estimation and suppress this warning.
  model_result = await model_client.create(


TaskResult(messages=[TextMessage(id='3c6a8bf3-c44a-4909-8364-1464d509ccf6', source='user', models_usage=None, metadata={}, created_at=datetime.datetime(2025, 7, 10, 14, 40, 41, 210209, tzinfo=datetime.timezone.utc), content='Write the functional specifications for a new product', type='TextMessage'), TextMessage(id='0a6f79e1-9d1d-40f8-8ea7-2ff9a847f467', source='planning_agent', models_usage=RequestUsage(prompt_tokens=180, completion_tokens=283), metadata={}, created_at=datetime.datetime(2025, 7, 10, 14, 40, 45, 452020, tzinfo=datetime.timezone.utc), content="To write functional specifications for a new product, we need to approach the task in the following steps:\n\n### Steps to Complete the Task:\n1. Understand the product requirements and objectives, as well as the target audience and use case. \n2. Summarize the key functional requirements.\n3. Create a functional specification document structure.\n4. Represent complex ideas visually using diagrams (if needed) to improve clarity.\n